## Описание данных

В качестве примера рассмотрим потребительские расходы на здравоохранение по регионам России за 2022 и 2023 годы. Они представлены в руб./мес. в среднем на члена 
домашнего хозяйств.

Источник данных: Росстат, Приложение 1. "Доходы, расходы и потребление домашних хозяйств по субъектам 
Российской Федераци", лист 1.4и
https://rosstat.gov.ru/storage/mediabank/Dohod_rashod_potreblen_3k-2023.htm

# Непараметрические оценки распределений

### Гистограммы

In [2]:
import pandas as pd

data = pd.read_excel("data.xlsx", sheet_name = "Data", index_col=0)
data.index.name = "region"

data

expense_3q2022  expense_3q2023  healthP_3q2022  \
region                                                                         
Белгородская область               21914.398       25241.122        2.568850   
Брянская область                   18265.001       19635.899        2.933966   
Владимирская область               19813.828       23137.913        3.588756   
Воронежская область                17621.889       19502.166        4.558280   
Ивановская область                 21681.452       23090.981        4.420234   
...                                      ...             ...             ...   
Амурская область                   19586.108       21720.673        5.966755   
Магаданская область                36153.698       64866.434        3.411275   
Сахалинская область                32652.890       32761.952        3.462753   
Еврейская автономная область       21690.199       25686.048        4.416723   
Чукотский автономный округ         34444.050       29854.794        3.193692   

                              healthP_3q2023  health_3q2022  health_3q2023  
region                                                                      
Белгородская область                2.994974        562.948        755.965  
Брянская область                    3.079054        535.889        604.600  
Владимирская область                3.879473        711.070        897.629  
Воронежская область                 4.991471        803.255        973.445  
Ивановская область                  5.235269        958.371       1208.875  
...                                      ...            ...            ...  
Амурская область                    3.962138       1168.655        860.603  
Магаданская область                 1.548055       1233.302       1004.168  
Сахалинская область                 4.333130       1130.689       1419.618  
Еврейская автономная область        3.795769        957.996        974.983  
Чукотский автономный округ          2.547809       1100.037        760.643  

[82 rows x 6 columns]

In [31]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Create a 1x2 subplot grid
fig = make_subplots(rows=1, cols=2, subplot_titles=[
    'Health expenses in 3Q2022 per h/h member',
    'Health expenses in 3Q2023 per h/h member'])

# First subplot: histogram for 3Q2022
fig.add_trace(go.Histogram(x=data.health_3q2022, autobinx=True), row=1, col=1)

# Second subplot: histogram for 3Q2023
fig.add_trace(go.Histogram(x=data.health_3q2023, autobinx=True), row=1, col=2)

# Update layout for the figure
fig.update_layout(height=500, width=1000, showlegend=False)

# Display the plot
fig.show()

In [32]:
X = data.health_3q2023

In [34]:
import plotly.graph_objects as go
import numpy as np
import plotly.express as px

def plot_hist(data=pd.Series):

    # Sample data (replace this with your actual data)

    # Define the start number of bins
    start_bins = 10

    # Create the histogram with a starting number of bins
    fig = go.Figure()

    # Add histogram trace
    fig.add_trace(go.Histogram(x=data, nbinsx=start_bins))

    # Define the slider steps
    slider_steps = [
        dict(
            method="update",
            args=[{"nbinsx": [bins]}],
            label=f"{bins} bins"
        )
        for bins in range(1, 83)
    ]

    # Update the layout to include a slider
    fig.update_layout(
        title_text='Health expenses in 3Q2023 per h/h member',
        xaxis_title_text='Expenses',
        yaxis_title_text='Count',
        sliders=[{
            "active": start_bins - 1,
            "currentvalue": {"prefix": "Number of bins: "},
            "pad": {"t": 50},
            "steps": slider_steps
        }],
        height=600,
        width=1000
    )

    # Display the plot
    fig.show()


plot_hist(X)

# Ядерная оценка плотности

1. Определение
2. Виды ядер (отличия от ядер из МО)
3. Иллюстрация

In [35]:
import plotly.graph_objects as go
import numpy as np
from scipy.stats import norm, gaussian_kde

cur_min = X.min()
cur_max = X.max()

# Create histogram
hist = go.Histogram(x=X, histnorm='probability density', name='Histogram', nbinsx=30)
bw_methods = ["scott", "silverman"]

x_vals = np.linspace(cur_min, cur_max, 1000)


# KDE traces
kde_traces = []
for method in bw_methods:

    kde = gaussian_kde(X, bw_method=method)
    
    kde_trace = go.Scatter(
        x=x_vals,
        y = kde.evaluate(x_vals), # Placeholder for actual KDE
        mode='lines',
        name=f'KDE ({method})',
        visible=False
    )
    kde_traces.append(kde_trace)

# Normal distribution trace
normal_trace = go.Scatter(
    x=x_vals,
    y=norm.pdf(x_vals, loc=np.mean(X), scale=np.std(X)),
    mode='lines',
    name='Normal Distribution',
    line=dict(dash='dash')
)

# Add all traces
fig = go.Figure(data=[hist, normal_trace] + kde_traces)

# Update layout with selector
fig.update_layout(
    height=600,
    width=1000,
    updatemenus=[
        dict(
            type="dropdown",
            direction="down",
            x=0.7,
            y=1.15,

            showactive=True,
            buttons=list([
                dict(label="None",
                     method="update",
                     args=[{"visible": [True, True] + [False] * len(bw_methods)},
                           {"title": ""}]),
                dict(label="scott",
                     method="update",
                     args=[{"visible": [True, True] + [method == 'scott' for method in bw_methods]},
                           {"title": "Gaussian KDE (scott)"}]),
                dict(label="silverman",
                     method="update",
                     args=[{"visible": [True, True] + [method == 'silverman' for method in bw_methods]},
                           {"title": "Gaussian KDE (silverman)"}]),

            ]),
        )
    ]
)

fig.show()


# Параметрические оценки

## Точечные оценки

In [23]:
# Вариационный ряд
variation_series = np.sort(X)

In [24]:
# 1-я порядковая статистика
variation_series[0]

np.float64(-3.0042115286919184)

In [25]:
# 10-я порядковая статистика
variation_series[10]

np.float64(-1.883799942459634)

In [ ]:
# Предполагаем некоторое распре

### Выборочные моменты

#### Начальные моменты

$$
\bar{X}^k = \frac{1}{n}\sum_{i=1}^{n} X^k_i
$$

In [26]:
# Первый начальный момент (Выборочное среднее)
X.sum() / len(X)

np.float64(-0.00014322161621088548)

In [27]:
# Второй начальный момент
(X**2).sum() / len(X)

np.float64(0.9619074816231915)

#### Центральные моменты

$$
\bar{S}^k = \frac{1}{n}\sum_{i=1}^{n} (X_i - \bar{X})^k
$$

In [28]:
# Первый центральный момент
(X - X.mean()).sum() / len(X)

np.float64(-1.2434497875801754e-17)

In [29]:
# Второй центральный момент (дисперсия)
((X - X.mean())**2).sum() / len(X)

np.float64(0.9619074611107602)

## Методы получения оценок

### Метод моментов

По гистограмме мы можем предположить класс распределений, которым соответствуют наши данные. Пусть мы сделали выбор в пользу $X_i \sim N(\mu, \sigma^2)$. Метод моментов устроен очень просто. Мы должны подобрать такие параметры, чтобы теоретические моменты были похожи на выборочные. Например, для нормального распределения нам нужно построить следующую систему уравнений:

$$
E(X_i) = \bar{X} \\
Var(X_i) = \bar{S}^{(2)}
$$

Для нормального распределения всё выражается очевидно:

$$
\hat{\mu} = \bar{X} \\
\hat{\sigma}^2 = \bar{S}^{(2)}
$$

Количество уравнений зависит от количества параметров. Например, у экспоненциального распределения только один параметр. Соответственно, понадобится только одно уравнение.

Для более сложных распределений уравнения уже не будут независимыми и придётся честно решать систему уравнений. Выбор моментов, по которым будут строиться уравнения, остаётся на выбор исследователя. Обычно стараются использовать наиболее простые моменты из доступных

In [42]:
mu_hat = X.mean()
sigma_sq = X.std() ** 2

In [46]:
cur_min = X.min()
cur_max = X.max()


# Create histogram
hist = go.Histogram(x=X, histnorm='probability density', name='Histogram', nbinsx=30)
bw_methods = ["scott", "silverman"]

x_vals = np.linspace(cur_min, cur_max, 1000)

# Normal distribution trace
normal_trace = go.Scatter(
    x=x_vals,
    y=norm.pdf(x_vals, loc=np.mean(X), scale=np.std(X)),
    mode='lines',
    name='Normal Distribution',
    line=dict(dash='dash')
)

# Add all traces
fig = go.Figure(data=[hist, normal_trace])

fig.update_layout(
        title_text='Health expenses in 3Q2023 per h/h member',
        xaxis_title_text='Expenses',
        yaxis_title_text='Count',
        height=600,
        width=1000
    )

fig.show()

### Метод максимального правдоподобия

Мы подробно разбирали этот метод ранее, поэтому ограничимся только результатами. Для нормальной выборки максимум правдоподобия будет выглядеть аналогично методу моментов.

$$
\hat{\mu} = \bar{X} \\
\hat{\sigma}^2 = \bar{S}^{(2)}
$$


## Свойства точечных оценок

### Несмещённость

Оценка это функция от выборки. Так как выборка -- случайная величина, то и оценка тоже является случайной. Несмещённая оценка в среднем по всем возможным выборкам должна давать истинный параметр.

$$
\mathbb{E}_X(\hat{\theta}(X)) = \theta
$$

In [54]:
mean = 0
std = 1
n=100

n_samples = 10000
samples = [
    np.random.normal(loc=mean, scale=std, size=100) for _ in range(n_samples)
]

mu_hats = [sample.mean() for sample in samples]

np.mean(mu_hats)


np.float64(0.0003030862234012726)

### Эффективность

В общем случае оценка $\theta_1$ считается более эффективной чем $\theta_2$, если

$$
\mathbb{E}(\hat{\theta}_1 - \theta) \leq \mathbb{E}(\hat{\theta}_2 - \theta)
$$

Для несмещённых оценок это неравенство можно переписать в терминах дисперсии, так как $\mathbb{E}(\hat{\theta}) = \theta$:

$$
\mathbb{Var}(\theta_1) \leq \mathbb{Var}(\theta_2)
$$

Такую эффективность называют относительной.

Так как в реальных задачах мы истинное значение параметра $\theta$ не знаем, сравнивать эффективность оценок сложно. Можно использовать оценки этих величин, но в ряде задач для оценок можно теоретически доказать, что они наиболее эффективные в своём классе. Подробнее мы поговорим об этом в разделе эконометрики, когда будем обсуждать BLUE-оценки.

### Состоятельность

In [97]:
max_sample_size =100000 

samples = [
    np.random.normal(loc=mean, scale=std, size=i) for i in range(0, max_sample_size, 100)
]

mu_hats = np.array([sample.mean() for sample in samples])

diffs = np.abs(mu_hats - mean)

# Normal distribution trace
diff_plot = go.Scatter(
    x=list(range(max_sample_size)),
    y=diffs,
    mode='lines',
    name='Diff'
)

def moving_average(x, w):
    return np.convolve(x, np.ones(w), 'valid') / w

# Normal distribution trace
smoothed_diff_plot = go.Scatter(
    x=list(range(max_sample_size)),
    y=moving_average(diffs, 20),
    mode='lines',
    name='Smoothed diff'
)
# Add all traces
fig = go.Figure(data=[ diff_plot, smoothed_diff_plot])


fig.update_layout(
        title_text='Mu estimation deviation',
        xaxis_title_text='Absolute error',
        yaxis_title_text='Sample size',
        height=600,
        width=1000
    )

fig.show()


/var/folders/cp/4bl3kvm10tl3r81sxqkgg1q00000gn/T/ipykernel_5417/1513641346.py:7: RuntimeWarning:

Mean of empty slice.

/Users/mszekhov/Desktop/current_projects/hse_asml_course/venv/lib/python3.10/site-packages/numpy/_core/_methods.py:138: RuntimeWarning:

invalid value encountered in scalar divide



### Сходимость к некоторому распределению

При некоторых обстоятельствах распределения оценок могут сходиться к какому-то конкретному распределению. Так, оценки метода максимального правдоподобия асимптотически нормальны. Мы легко это увидим, посимулировав выборки одинакового размера.

In [84]:
n_samples = 10000
samples = [
    np.random.normal(loc=mean, scale=std, size=100) for _ in range(n_samples)
]

mu_hats = [sample.mean() for sample in samples]
std_hats = [sample.std() for sample in samples]



In [85]:
cur_min = np.min(mu_hats)
cur_max = np.max(mu_hats)


x_vals = np.linspace(cur_min, cur_max, 1000)
# Create histogram
hist = go.Histogram(x=mu_hats, histnorm='probability density', name='Histogram', nbinsx=50)

# Normal distribution trace
normal_trace = go.Scatter(
    x=x_vals,
    y=norm.pdf(x_vals, loc=np.mean(mu_hats), scale=np.std(mu_hats)),
    mode='lines',
    name='Normal Distribution'
)

# Add all traces
fig = go.Figure(data=[hist, normal_trace])


fig.update_layout(
        title_text='Mu estimations distribution',
        xaxis_title_text='Expenses',
        yaxis_title_text='Count',
        height=600,
        width=1000
    )

fig.show()

In [88]:
cur_min = np.min(std_hats)
cur_max = np.max(std_hats)


x_vals = np.linspace(cur_min, cur_max, 1000)
# Create histogram
hist = go.Histogram(x=std_hats, histnorm='probability density', name='Histogram', nbinsx=50)

# Normal distribution trace
normal_trace = go.Scatter(
    x=x_vals,
    y=norm.pdf(x_vals, loc=np.mean(std_hats), scale=np.std(std_hats)),
    mode='lines',
    name='Normal Distribution'
)

# Add all traces
fig = go.Figure(data=[hist, normal_trace])


fig.update_layout(
        title_text='Sigma estimations distribution',
        height=600,
        width=1000
    )

fig.show()

## Свойства и особенности оценок основных методов

### Метод моментов
1. Ассимптотическая несмещённость
2. Ассимптотическая нормальность

### Метод максимального правдоподобия
1. Инвариантность относительно гладкого преобразования $g$:

    Если существует $\hat{\theta}_{ML}$, то $\hat{g(\theta)} = g(\hat{\theta})$

2. Пусть L -- функция правдоподобия. Если существует единственный максимум у L, $\exists L_{\theta}'''$ и случай регулярный, то

    1. $\hat{\theta}_{ML}$ состоятельна
    2. $\hat{\theta}_{ML}$ асимптотически несмещена
    3. $\hat{\theta}_{ML}$ асимптотически эффективна
    4. $\hat{\theta}_{ML}$ асимптотически нормальна


##